In [2]:
import os
import sys
from glob import glob

module_path = os.path.abspath(os.path.join('../../'))
if module_path not in sys.path:
    sys.path.append(module_path)
    
import desispec
from desispec.io import read_spectra, write_spectra
from desispec.spectra import Spectra

from desiutil.log import get_logger, DEBUG

from desidiff.src.group_tiles import *
from desidiff.src.dates_to_process import *
from desidiff.src.coadd import *
from desidiff.src.scores import *
from desidiff.src.ContinuumFitFilter_desidiff import *

from timedomain.sp_utils import SkyPortal as sp
import requests
import datetime
import heapq
import time
import copy
import numpy
from astropy.time import Time
from astropy.table import Table, vstack, unique, SortedArray
import h5py

%matplotlib inline
import matplotlib.pyplot as plt
from matplotlib.backends.backend_pdf import PdfPages
from IPython import display

In [3]:
#SkyPortal token:
secret_file = "/global/cfs/cdirs/desi/science/td/secrets/desidiff_sp.txt"
with open(secret_file, 'r') as file:
    token = file.read().replace('\n', '')
headers = {'Authorization': f'token {token}'}

filter_name = 'DESIDIFF'
start_time = time.time()

In [3]:
night_arr = getUnprocessedDates()
all_plots_pdf = PdfPages("All_plots.pdf")

len(night_arr): 240
--- get unprocessed dates took:  142.0846643447876 seconds ---


In [ ]:
# read in and store in one place all the fibermap information in the spectra files
#night_arr = getUnprocessedDates()

for night in night_arr:   
    for current_filename in glob(f"/global/project/projectdirs/desi/spectro/redux/daily/tiles/cumulative/*/{night}/spectra-*.fits"):
        tile = current_filename.split('/')[-3]
        petal = current_filename.split('-')[1]
        ### daily_spectra, the precursor to current spectra, before coadding, to select night, unique target ids, and individual target ids
        ### spectra.select functionality will not work once coadded with coaddition.coadd_cameras
        try:
            daily_spectra = ((read_spectra(current_filename)).select(nights = night))
        except:
            daily_spectra = ((read_spectra(current_filename)).select(nights = (night-1)))

        table = Table.read(current_filename, format='fits',hdu=1, memmap=True) 
        ##### DAVE'S ADDITION ##############
        targetcols = [i for i in table.colnames if i[-7:] =='_TARGET']
        nonzerocheck = [True in k for k in [[j != 0 for j in table[targetcols][i]] for i in range(len(table))]]
        #a really ugly line, basically generates a list of bools, 
        #True if there is at least one nonzero element in all columns ending in _TARGET
        table.remove_rows([i for i, val in enumerate(nonzerocheck) if not val])
        #This gets the index of all False values from the previous list and removes those rows
        table = table['TARGETID','TARGET_RA','TARGET_DEC','TILEID','OBJTYPE','PETAL_LOC','FIBERSTATUS','NIGHT']
        ######## END DAVE'S ADDITION ############
        table = table[numpy.logical_and(table['OBJTYPE']=='TGT', table['FIBERSTATUS']==0)]


        for ref_filename in glob(f"/global/cfs/cdirs/desi/spectro/redux/*/tiles/cumulative/{tile}/*/coadd-{petal}-{tile}*.fits"):
            print(ref_filename)

            if ref_filename.split('/')[-6] == 'fuji' or ref_filename.split('/')[-6] == 'guadalupe':
                prev_spectra = read_spectra(ref_filename)
                ### creates a pdf whether or not any spectra on tile passes filters
                pdf_per_tile = PdfPages(str(tile)+".pdf")

                gen = (t for t in daily_spectra.target_ids()[numpy.where(numpy.logical_and(daily_spectra.fibermap['OBJTYPE']=='TGT', daily_spectra.fibermap['FIBERSTATUS']==0))] if t in prev_spectra.target_ids()[numpy.where(prev_spectra.fibermap['OBJTYPE']=='TGT')])
                for t in gen:
                    print(t)
                    ### grab ra and dec values for use in SkyPortal functionality later
                    #ra_dec = (table[table['TARGETID']==t]['TARGET_RA'][0], table[table['TARGETID']==t]['TARGET_DEC'][0])
                    ra, dec = table['TARGETID' == t]['TARGET_RA'], table['TARGETID' == t]['TARGET_DEC']
                    ### match target ids
                    current_spectra = desispec.coaddition.coadd_cameras(daily_spectra.select(targets = t))
                    ref_spectra = desispec.coaddition.coadd_cameras(prev_spectra.select(targets = t))

                    norm = normalization(current_spectra.flux, current_spectra.mask, ref_spectra.flux, ref_spectra.mask)

                    # need to instantiate a Spectra object for the difference. 
                    ### Using 'dif_spectra = Spectra()' is bugging on dif_spectra.mask type=NoneType, can't assign.
                    #### dif_spectra = current_spectra
                    ### copy.deepcopy() is deprecated as memory expensive
                    dif_spectra = copy.deepcopy(current_spectra)
                    #### any problem with hardcoding in 'brz' for key in the following:
                    for key in (current_spectra.flux).keys():
                        current_spectra.flux[key] = current_spectra.flux[key]/norm
                        current_spectra.ivar[key] = current_spectra.ivar[key]*norm**2 
                        # subtraction of current and reference fluxes
                        dif_spectra.flux[key] = current_spectra.flux[key] - ref_spectra.flux[key]
                        ### couldn't dif_spectra.mask[key] == 2 by summing current.mask and reference.mask
                        # summation of current and reference masks
                        dif_spectra.mask[key] = current_spectra.mask[key] + ref_spectra.mask[key]
                        # inverted summation of current and spectra inverse variance
                        ### still returning RuntimeWarning: divide by zero encountered in true_divide but not in infinite loop for the moment
                        dif_spectra.ivar[key] = 1./(1./current_spectra.ivar[key] + 1./ref_spectra.ivar[key])

                    # mean-subtracted difference
                    dif_flux_clipped = clipmean(dif_spectra.flux, dif_spectra.ivar, dif_spectra.mask)

                    # filters 
                    # Difference spectrum may have broadband signal
                    perband_filter = perband_SN(dif_flux_clipped, dif_spectra.ivar, dif_spectra.mask)

                    # fractional increase
                    perband_inc = perband_increase(dif_flux_clipped, dif_spectra.ivar, dif_spectra.mask, ref_spectra.flux, ref_spectra.ivar, ref_spectra.mask)

                    # Difference spectrum may have high-frequency signal
                    perres_filter_broad = perconv_SN(dif_flux_clipped, dif_spectra.ivar, dif_spectra.mask, ncon = 100, nsig = 17)

                    perres_filter_narrow = perconv_SN(dif_flux_clipped, dif_spectra.ivar, dif_spectra.mask, ncon = 5, nsig = 10)
                    ### grab redrock data required for filters using redshift (zinfo)
                    current_filename = (current_filename.replace('spectra','redrock')).replace('fits', 'h5')

                    with h5py.File(current_filename, "r") as f:
                        zinfo = f['zfit'][str(t)]['zfit'][0]['z']

                    # Search for signature lines of TDEs, only interested in Galaxies
                    linetable = line_finder(dif_spectra.wave, dif_flux_clipped, dif_spectra.ivar, dif_spectra.mask, zinfo)
                    # print(night, linetable)
                    Hline_score = Hline_filter(linetable)
                    # deriv_score = deriv_filter(dif_flux_clipped, dif_spectra.ivar,dif_spectra.mask)
                    #broadband
                    bblogic = any(numpy.logical_and(numpy.array(list(perband_filter.values()))>10, numpy.array(list(perband_inc.values()))>0.25))
                    narrowlinelogic = perres_filter_narrow >=2
                    broadlinelogic = perres_filter_broad >=3
                    # TDElogic = any([TDE_score == 2, TDE_score == 3, TDE_score == 4, TDE_score == 5])
                    Hlinelogic = any([Hline_score >= 1])
                    # derivlogic = any([deriv_score >= 3])
                    logic = [bblogic, narrowlinelogic,  broadlinelogic, Hlinelogic]
                    logic_name = ['Broadband', 'narrow line', 'broad line','Hline'] #must be in same order as logic!, use as mask
                    logic_name = numpy.ma.masked_array(logic_name, mask = [not i for i in logic])

                    plt.clf()

                    plt.rcParams["figure.figsize"] = (20,6)
                    if any(logic):
                        processed(t, tile, night)
                        plt.figure()
                        for key in (current_spectra.flux).keys():
                            w=numpy.where(dif_spectra.mask[key][0] == 0)

                            plt.plot(dif_spectra.wave[key][w], dif_spectra.flux[key][0][w], color='red', label = 'Difference')
                            plt.plot(current_spectra.wave[key][w], current_spectra.flux[key][0][w], color='blue', alpha=0.5, label = 'New Spectrum')
                            plt.plot(ref_spectra.wave[key][w],ref_spectra.flux[key][0][w],color='green',alpha=0.5, label = 'Reference Spectrum')

                            plt.legend()
                            plt.xlabel('Wavelength (Å)')
                            plt.ylabel('Flux') 
                            plt.title(str(t) + "  " + str(night) + "  " + str(tile)  + "  " + str(logic_name))
                            #plt.show()
                            plt.savefig(pdf_per_tile, format = 'pdf')
                            plt.savefig(all_plots_pdf, format = 'pdf')
                            plt.close()
                    """
                    #SkyPortal functionality begins:
                    #SkyPortal's Id for the object
                    objID = 'DESI{}'.format(str(t))

                    #Code to check if this object already exists in SkyPortal. If not, create it

                    response = requests.get("https://desi-skyportal.lbl.gov/api/candidates/{}".format(objID), headers={"Authorization": f"token {token}"})
                    if response.status_code == 400:
                        obj_data = {
                                "ra": ra, #RA is required when creating a new object.
                                "dec": dec, #Same for DEC
                                "id": objID,
                                "redshift": zinfo,
                                "filter_ids": [sp.filter_id(filter_name)],
                                "passed_at": str(datetime.datetime.utcnow()) #UTC time when the object passed the filter
                                }

                        response = requests.post(
                                "https://desi-skyportal.lbl.gov/api/candidates",
                                json = obj_data,
                                headers = {"Authorization": f"token {token}"})

                    #Now, we send the differenced spectrum to SkyPortal
                    #First, check if the same spectrum already exists under the object
                    response = requests.get("https://desi-skyportal.lbl.gov/api/sources/{}/spectra".format(objID),headers={"Authorization": f"token {token}"})
                    post = True
                    # for i in range (len(response.json()['data']['spectra'])):
                    #     if (wavelengths == response.json()['data']['spectra'][i]['wavelengths'] and flux == response.json()['data']['spectra'][i]['fluxes']):
                    #         post = False
                    #Only if the exact same spectrum doesn't already exist, upload it.
                    if post:
                        #Send difference spectrum to SP:
                        dif_spectrum_data = {
                                "obj_id": objID,
                                "wavelengths": dif_spectra.wave['brz'][w].tolist(),
                                "fluxes": dif_spectra.flux['brz'][0][w].tolist(),
                                "observed_at": str(night)[:4]+'-'+str(night)[4:6]+'-'+str(night)[6:]+' '+'00:00:00.000000', # Date converted into UTC time format
                                "origin": "DESIDIFF_dif_spectrum", #Only the difference spectrum gets this tag in order to distinguish it on SkyPortal
                                "group_ids": [sp.group_id("DESI")],
                                "instrument_id": sp.instrument_id()
                                }
                        response = requests.post(
                                    '{}/api/spectrum'.format(sp.url),
                                    json= dif_spectrum_data,
                                    headers={"Authorization": f"token {token}"}) 

                        #Send new spectra to SP:
                        current_spectra_data = {
                            "obj_id": objID,
                            "wavelengths":current_spectra.wave['brz'][w].tolist(),
                            "fluxes": current_spectra.flux['brz'][0][w].tolist(),
                            "observed_at": str(night)[:4]+'-'+str(night)[4:6]+'-'+str(night)[6:]+' '+'00:00:00.000000', # Date converted into UTC time format
                            "origin": "DESIDIFF",
                            "group_ids": [sp.group_id("DESI")],
                            "instrument_id": sp.instrument_id()
                            }
                        response = requests.post(
                                '{}/api/spectrum'.format(sp.url),
                                json= current_spectra_data,
                                headers={"Authorization": f"token {token}"}) 

                        #Code to find the ref_night that is closest to current_night to be used as 'observed_at' for SP
                        if ref_filename.split('/')[-6] == 'fuji':
                            ref_night = 20201214
                        elif ref_filename.split('/')[-6] == 'guadalupe':
                            ref_night = 20210514
                        current_night = datetime.datetime(int(str(night)[:4]), int(str(night)[4:6]), int(str(night)[6:]))
                        closest_night = datetime.datetime(int(str(ref_night)[:4]), int(str(ref_night)[4:6]), int(str(ref_night)[6:]))



                        ref_spectra_data = {
                            "obj_id": objID,
                            "wavelengths": ref_spectra.wave['brz'][w].tolist(),
                            "fluxes": ref_spectra.flux['brz'][0][w].tolist(),
                            "observed_at": str(closest_night),
                            "origin": "DESIDIFF",
                            "group_ids": [sp.group_id("DESI")],
                            "instrument_id": sp.instrument_id()
                            }
                        response = requests.post(
                                '{}/api/spectrum'.format(sp.url),
                                json= ref_spectra_data,
                                headers={"Authorization": f"token {token}"})    
                    """
    pdf_per_tile.close()
all_plots_pdf.close()
                        
            

INFO:spectra.py:291:read_spectra: iotime 0.515 sec to read spectra-5-21163-thru20210607.fits at 2022-07-11T11:51:40.655835
/global/cfs/cdirs/desi/spectro/redux/everest/tiles/cumulative/21163/20210607/coadd-5-21163-thru20210607.fits
/global/cfs/cdirs/desi/spectro/redux/daily/tiles/cumulative/21163/20210607/coadd-5-21163-thru20210607.fits
/global/cfs/cdirs/desi/spectro/redux/guadalupe/tiles/cumulative/21163/20210607/coadd-5-21163-thru20210607.fits
INFO:spectra.py:291:read_spectra: iotime 0.396 sec to read coadd-5-21163-thru20210607.fits at 2022-07-11T11:51:42.576905
39633039680077974


/tmp/ipykernel_23063/324525585.py:64: RuntimeWarning: divide by zero encountered in true_divide
  dif_spectra.ivar[key] = 1./(1./current_spectra.ivar[key] + 1./ref_spectra.ivar[key])
/global/cscratch1/sd/clepart/timedomain/desidiff/src/scores.py:76: RuntimeWarning: divide by zero encountered in true_divide
  newston[b]=numpy.array(numpy.convolve(newy[b][0], conk, mode='valid') / numpy.sqrt(numpy.convolve(1/ivar[b][0], conk, mode='valid')))
/global/cscratch1/sd/clepart/timedomain/desidiff/src/ContinuumFitFilter_desidiff.py:99: RuntimeWarning: divide by zero encountered in true_divide
  Hasigma = 1/np.sqrt(Haivar)
/global/common/software/desi/cori/desiconda/20211217-2.0.0/conda/lib/python3.9/site-packages/scipy/optimize/minpack.py:833: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',


39633039680080750


/tmp/ipykernel_23063/324525585.py:64: RuntimeWarning: divide by zero encountered in true_divide
  dif_spectra.ivar[key] = 1./(1./current_spectra.ivar[key] + 1./ref_spectra.ivar[key])
/global/cscratch1/sd/clepart/timedomain/desidiff/src/scores.py:76: RuntimeWarning: divide by zero encountered in true_divide
  newston[b]=numpy.array(numpy.convolve(newy[b][0], conk, mode='valid') / numpy.sqrt(numpy.convolve(1/ivar[b][0], conk, mode='valid')))
/global/cscratch1/sd/clepart/timedomain/desidiff/src/ContinuumFitFilter_desidiff.py:99: RuntimeWarning: divide by zero encountered in true_divide
  Hasigma = 1/np.sqrt(Haivar)


39633044444807766


...

39628113474229953


/global/cscratch1/sd/clepart/timedomain/desidiff/src/scores.py:76: RuntimeWarning: divide by zero encountered in true_divide
  newston[b]=numpy.array(numpy.convolve(newy[b][0], conk, mode='valid') / numpy.sqrt(numpy.convolve(1/ivar[b][0], conk, mode='valid')))
/global/cscratch1/sd/clepart/timedomain/desidiff/src/ContinuumFitFilter_desidiff.py:99: RuntimeWarning: divide by zero encountered in true_divide
  Hasigma = 1/np.sqrt(Haivar)
/global/cscratch1/sd/clepart/timedomain/desidiff/src/ContinuumFitFilter_desidiff.py:107: RuntimeWarning: divide by zero encountered in true_divide
  NIIIsigma = 1/np.sqrt(NIIIivar)
/tmp/ipykernel_23063/324525585.py:64: RuntimeWarning: divide by zero encountered in true_divide
  dif_spectra.ivar[key] = 1./(1./current_spectra.ivar[key] + 1./ref_spectra.ivar[key])


39628113474230286


/global/cscratch1/sd/clepart/timedomain/desidiff/src/scores.py:76: RuntimeWarning: divide by zero encountered in true_divide
  newston[b]=numpy.array(numpy.convolve(newy[b][0], conk, mode='valid') / numpy.sqrt(numpy.convolve(1/ivar[b][0], conk, mode='valid')))
/global/cscratch1/sd/clepart/timedomain/desidiff/src/ContinuumFitFilter_desidiff.py:90: RuntimeWarning: divide by zero encountered in true_divide
  HBsigma = 1/np.sqrt(HBivar)
/global/cscratch1/sd/clepart/timedomain/desidiff/src/ContinuumFitFilter_desidiff.py:99: RuntimeWarning: divide by zero encountered in true_divide
  Hasigma = 1/np.sqrt(Haivar)
/global/cscratch1/sd/clepart/timedomain/desidiff/src/ContinuumFitFilter_desidiff.py:107: RuntimeWarning: divide by zero encountered in true_divide
  NIIIsigma = 1/np.sqrt(NIIIivar)
/global/common/software/desi/cori/desiconda/20211217-2.0.0/conda/lib/python3.9/site-packages/scipy/optimize/minpack.py:833: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.wa

39628113478421024


In [9]:
print(ra_dec)

(264.79014464874683, 33.735652626899395)


NameError: name 'gen' is not defined